In [2]:
############### propuplate the trigger fits
import h5py, pylab, numpy, glob, os.path

fits = {}
ftimes = {}
for ifo in ['H1', 'L1', 'V1']:
    fits[ifo] = []
    ftimes[ifo] = []

fnames = glob.glob('./fits/*.hdf')
for fname in fnames:
    name = os.path.basename(fname)
    ifo = name.split('-')[0]
    start = int(name.split('-')[2])
    dur = int(name.split('-')[3].split('.')[0])
    
    f = h5py.File(fname, 'r')
    
    alpha = f['fit_coeff'][:]
    count = f['count_in_template'][:]
    
    ftimes[ifo].append(start)
    fits[ifo].append((alpha, count))
    
for ifo in ["H1", "L1"]:
    ftimes[ifo] = numpy.array(ftimes[ifo])
    
def getnoiserate(time, stat, tid, ifo):
    s = ftimes[ifo]
    d = time - s
    l = numpy.where(d >= 0)[0]
    v = l[d[l].argmin()]
    
    alpha, count = fits[ifo][v]
    
    alphai = alpha[tid]
    ratei = count[tid]
    thresh = 5.9
    lognoisel = - alphai * (stat - thresh) + numpy.log(alphai) + numpy.log(ratei)
    return lognoisel
#getfit(1186624818, 10, 0, 'H1')

In [3]:
import h5py, pylab, numpy
from pycbc.events.ranking import newsnr_sgveto_psdvar_scaled_threshold
from pycbc.events.coinc import cluster_over_time
from pycbc.events.veto import indices_within_segments, segments_to_start_end, indices_outside_times, indices_within_times
from pycbc.dq import query_flag
from pycbc.conversions import mchirp_from_mass1_mass2

times = {}
nsnrs = {}
data = {}

for run in ['bns', 'nsbh', 'bbh']:
    for ifo in ['H1', 'L1']:
        print(run, ifo)

        b = h5py.File('./{}.hdf'.format(run), 'r')
        m1 = b['mass1'][:]
        m2 = b['mass2'][:]
        mt = m1 + m2
        mc = mchirp_from_mass1_mass2(m1, m2)

        
        # Apply signal consistency tests
        f = h5py.File('./o1o2o3a_{}{}.hdf'.format(run, ifo), 'r')
        snr = f['snr'][:]
        chisq = f['chisq'][:] / (f['chisq_dof'][:] * 2 - 2)
        psd_var = f['psd_var_val'][:]
        time = f['end_time'][:]
        tid = f['template_id'][:]
        sg = f['sg_chisq'][:]
    
        f = h5py.File('./o3b_{}{}.hdf'.format(run, ifo), 'r')
        snr = numpy.append(snr, f['snr'][:])
        chisq = numpy.append(chisq, f['chisq'][:] / (f['chisq_dof'][:] * 2 - 2))
        psd_var = numpy.append(psd_var, f['psd_var_val'][:])
        time = numpy.append(time, f['end_time'][:])
        tid = numpy.append(tid, f['template_id'][:])
        sg = numpy.append(sg, f['sg_chisq'][:])
        
        nsnr = newsnr_sgveto_psdvar_scaled_threshold(snr, chisq, sg, psd_var, threshold=1.8)

        # apply lcustering
        k = cluster_over_time(nsnr, time, 5.0)
        time = time[k]
        nsnr = nsnr[k]
        tid = tid[k]
        chisq = chisq[k]
        sg = sg[k]
        snr = snr[k]
        
        k = nsnr > 7
        time = time[k]
        nsnr = nsnr[k]
        tid = tid[k]
        chisq = chisq[k]
        sg = sg[k]  
        snr = snr[k]
        
        # Apply volume sensitivity prior
        r = h5py.File('./range.hdf', 'r')
        rifo = r['ifo'][:]
        rstart = r['start'][:]
        dist = r['range'][:]

        distr = dist / dist.max()
        volr = distr ** 3.0
        
        s = rstart.argsort()
        rstart = rstart[s]
        rifo = rifo[s]
        volr = volr[s]
        rstart = rstart[rifo == ifo.encode()]
        volr = volr[rifo == ifo.encode()]  
        l = numpy.searchsorted(rstart, time) - 1
        vfac = volr[l]

        # Apply mass prior
        if run == 'bbh':
            k = (mt[tid] < 130) & (sg < 3.6) 
            
            time = time[k]
            nsnr = nsnr[k]
            tid = tid[k]
            chisq = chisq[k]
            sg = sg[k]
            snr = snr[k]
            vfac = vfac[k]
            
            pfac = (mc[tid] / 20.0) ** 11.0 / 3.0
            nrate = []
            for p in zip(time, nsnr, tid):
                nrate.append(getnoiserate(*p, ifo))
            nrate = numpy.array(nrate)
            nsnr =  numpy.log(pfac) + numpy.log(vfac) - nrate
        elif run == 'nsbh':
            k = (mt[tid] < 50) & (sg < 3.6)            
            time = time[k]
            nsnr = nsnr[k]
            tid = tid[k]
            chisq = chisq[k]
            sg = sg[k]
            snr = snr[k]
            vfac = vfac[k]
            
            l = abs(time - 1263097407.74).argmin()
            print(time[l], snr[l], chisq[l], sg[l])
            
            #pfac = (mc[tid] / 20.0) ** 11.0 / 3.0
            #nrate = []
            #for p in zip(time, nsnr, tid):
            #    nrate.append(getnoiserate(*p, ifo))
            #nrate = numpy.array(nrate)
            #nsnr =  numpy.log(pfac) + numpy.log(vfac) - nrate              
        else:
            nsnr = (nsnr **2.0 + 2 * numpy.log(vfac)) ** 0.5
        
        # Remove hardware injections
        segs = []
        for s, e in [(1126051217, 1137254417), (1164556817, 1187733618), (1238166018, 1253977218), (1253977219, 1320363336)]:
            if ifo == 'V1' and s == 1126051217:
                continue
            segs +=  query_flag(ifo, 'CBC_HW_INJ', s, e, cache=True)
        
        # veto time aroung gates
        gtime = h5py.File('gates.hdf', 'r')[ifo][:]
        #gtime2 = h5py.File('/home/ahnitz/projects/3ogc/singles/gates.hdf', 'r')[ifo][:]
        #gtime = numpy.concatenate([gtime1, gtime2])
        
        s, e = segments_to_start_end(segs)
        s = numpy.concatenate([s, gtime - 0.5])
        e = numpy.concatenate([e, gtime + 0.5])

        #if run == 'bbh':
        #    o = h5py.File('./segs.hdf', 'a')
        #   o['{}/start'.format(ifo)] = s
        #    o['{}/end'.format(ifo)] = e
        #    o.close()
        #o = h5py.File('./segs.hdf', 'r')
        #s = o[ifo]['start'][:]
        #e = o[ifo]['end'][:]
        k = indices_outside_times(time, s, e)     
         
        time = time[k]
        nsnr = nsnr[k]
        tid = tid[k]
        chisq = chisq[k]
        sg = sg[k]
        snr = snr[k]
            
        print(len(snr))
        o = h5py.File('{}_{}_trigs.hdf'.format(run, ifo), 'w')
        o['stat'] = nsnr
        o['time'] = time
        o['chisq'] = chisq
        o['sg_chisq'] = sg
        o['snr'] = snr
        o['tid'] = tid
        o.close()
        
        times[(run, ifo)] = time
        nsnrs[(run, ifo)] = nsnr
        data[(run, ifo)] = time, nsnr, tid, chisq, sg, m1[tid], m2[tid], snr

bns H1
12396
bns L1


11544
nsbh H1
1263097521.8657227 7.4157867 1.0154760451543898 1.5426083
121026
nsbh L1
1263097407.7373047 8.808749 0.9890009857887445 1.0
131832
bbh H1
2500
bbh L1
2732


In [50]:
from pycbc.catalog import Catalog
from pycbc.events.veto import start_end_to_segments, segments_to_start_end
from pycbc.events.veto import indices_within_times
from astropy.time import Time

# get coinc HL time so we can select that for use as background
hsegs = []
lsegs = []
for s, e in [(1126051217, 1137254417),
             (1164556817, 1187733618),
             (1238166018, 1253977218),
             (1253977219, 1320363336)]:
    hsegs +=  query_flag('H1', 'DATA', s, e, cache=True)
    lsegs +=  query_flag('L1', 'DATA', s, e, cache=True)

cseg = (hsegs & lsegs).coalesce()
cstart, cend = segments_to_start_end(cseg)
cstart.sort()
cend.sort()
print((cend - cstart).sum())

    
c1 = Catalog(source='gwtc-2')
c2 = Catalog(source='gwtc-1')
c3 = Catalog(source='gwtc-3')

te = []
for c in [c1, c2, c3]:
    for m in c:
        if '190425' in m:
            continue
        te.append(c.mergers[m].time)
        
te += [1169069154.5756836, 1185152688.0356445]
te = numpy.array(te)

te = numpy.delete(te, abs(te - 1240164426).argmin())
te = numpy.delete(te, abs(te - 1245035079.312).argmin())
te = numpy.delete(te, abs(te - 1246663515.384).argmin())
te = numpy.delete(te, abs(te - 1252150105.324).argmin())

for k in [1262879936.0908203, 1267149509.5180664]:
    te = numpy.delete(te, abs(te - k).argmin())

from astropy.time import Time
import numpy

pylab.rc('text', usetex=True)
f, axs = pylab.subplots(2, 1, dpi=200, sharex=True, sharey=True)


for i1, run in enumerate(['bbh']):
    for i2, ifo in enumerate(['H1', 'L1']):
        pylab.sca(axs[i2]) 
   
        if ifo == 'H1':
            pylab.text(.5,.9, run.upper(), fontsize=15,
                   horizontalalignment='center',
                   transform=pylab.gca().transAxes)
            
        t, s, vtid, vchisq, vsg, m1, m2, snr = data[(run, ifo)]    
        #k = m1 + m2 < 150
        #t = t[k]
        #s = s[k]
        #m1 = m1[k]
        #m2 = m2[k]
        #vchisq = vchisq[k]
        #vsg = vsg[k]
        #snr = snr[k]
     
        gws = indices_within_times(t, te - 1.0, te + 1.0)
        nongw = indices_outside_times(t, te - 1.0, te + 1.0)
        
        hl = indices_within_times(t, cstart, cend)
        
        gws = gws[numpy.isin(gws, hl)]
        
        bkg = nongw[numpy.isin(nongw, hl)]
        can = nongw[~numpy.isin(nongw, hl)]
        
        bkg = bkg[indices_within_times(t[bkg], [1238166018], [1320363336])]
        gws = gws[indices_within_times(t[gws], [1238166018], [1320363336])]
        can = can[indices_within_times(t[can], [1238166018], [1320363336])] 

        print("GWNUM", (s[gws] > 0).sum())    
        bins = numpy.arange(-10, s.max()*1.2, 1.5)
        
        pylab.hist([s[bkg], s[can],  s[gws]], bins=bins,
                   label=('Background','Candidates',  'Multi-detector GWs', ), alpha=1.0, stacked=True, histtype='bar')
        
        pylab.yscale('log')
        pylab.xlim(xmin=-10, xmax=70)
        
        
        if i2 == 0:
            pylab.legend()
            pylab.text(-5, 35, "LIGO Hanford")
        else:
            pylab.text(-5, 35, "LIGO Livingston")
            pylab.xlabel('Ranking Statistic ($\Lambda_{s}$)', fontsize=14)
        pylab.ylabel('Counts', fontsize=14)
        #pylab.grid()
        

        f = h5py.File('./signal.hdf', 'r')
        sigw = f[ifo]['w'][:]
        sigs = f[ifo]['s'][:]
        bstat = s[bkg].max()
        
        pylab.gca().tick_params(axis='both', which='major', labelsize=12)
            
        #print(run, ifo, bstat)
        #print()
        top = s[can].argsort()[-10:]
        
        pastros = []
        times = []
        pnum = 0
        for i in top:
            stat =  s[can][i]
            scount = sigw[(sigs > bstat) & (sigs < stat)].sum()
            #print(scount)
            pastro = (scount / (1 + scount))
            pastros.append(pastro)
            times.append(t[can][i])
            
            if pastro >= 0.5:
                dt = Time(t[can][i], scale='utc', format='gps').datetime
                
                name = 'GW{:02d}{:02d}{:02d}\_{:02d}{:02d}{:02d}'.format(dt.year-2000,
                                                     dt.month,
                                                     dt.day,
                                                     dt.hour,
                                                     dt.minute,
                                                     dt.second,
                                                    )
                if ifo == 'H1':
                    astart = 5
                else:
                    astart = 30
                pylab.annotate(name, xy=(stat, 1.2), xytext=(stat, astart /  1.8 ** pnum),
                               arrowprops=dict(facecolor='black', frac=.001,
                                               headwidth=4, width=1, alpha=0.25),
                               )
                pnum += 1
            
            dt = Time(t[can][i], format='gps', scale='utc').datetime
            print("%s, %s, %2.2f %2.2f %2.2f %2.2f %2.2f %2.2f %2.2f" % (dt,  t[can][i],
                    stat, snr[can][i], vchisq[can][i], vsg[can][i], m1[can][i], m2[can][i], pastro))
            
        o = h5py.File('./pastro_{}_{}_single.hdf'.format(ifo, run), 'w')
        o['pastro'] = numpy.array(pastros)
        o['time'] = numpy.array(times)
        o.close()
        
pylab.tight_layout()
pylab.show()
pylab.savefig('bbh_single.pdf')

32004597
GWNUM 17
2019-12-17 09:16:26.895508, 1260609404.8955078, 0.65 7.27 1.00 1.80 49.43 65.75 0.00
2019-11-14 22:50:30.396973, 1257807048.3969727, 1.27 8.57 1.37 0.19 38.01 53.05 0.00
2019-12-17 12:31:10.949219, 1260621088.9492188, 2.18 9.08 1.37 1.30 45.81 81.08 0.00
2020-01-16 18:33:09.639160, 1263234807.6391602, 2.42 8.55 1.64 1.94 46.91 49.21 0.00
2019-04-19 07:11:42.229980, 1239693120.2299805, 3.32 8.16 1.33 3.14 65.70 61.59 0.00
2019-11-03 09:19:14.316406, 1256807972.3164062, 5.25 7.81 0.83 0.93 35.78 69.61 0.00
2019-05-19 04:29:37.591797, 1242275395.5917969, 5.53 9.40 1.53 3.03 74.14 49.66 0.00
2019-06-26 05:57:26.183105, 1245563864.1831055, 8.11 9.11 1.14 2.37 46.09 65.00 0.00
2019-05-23 00:54:18.338379, 1242608076.338379, 10.27 9.15 1.24 1.45 56.54 45.95 0.00
2020-03-02 01:58:11.518066, 1267149509.5180664, 27.32 10.52 1.00 1.05 38.57 40.46 0.66
GWNUM 18
2019-05-23 18:54:02.857910, 1242672860.8579102, 0.85 7.40 0.97 1.10 45.10 71.17 0.00
2019-08-21 17:42:39.587891, 12504445

/tmp/ipykernel_139522/537988127.py:156: UserWarning: 'frac' option in 'arrowprops' is no longer supported; use 'headlength' to set the head length in points.
  pylab.tight_layout()
/tmp/ipykernel_139522/537988127.py:157: UserWarning: Matplotlib is currently using agg, which is a non-GUI backend, so cannot show the figure.
  pylab.show()
/tmp/ipykernel_139522/537988127.py:158: UserWarning: 'frac' option in 'arrowprops' is no longer supported; use 'headlength' to set the head length in points.
  pylab.savefig('bbh_single.pdf')


In [51]:
from pycbc.catalog import Catalog
from pycbc.events.veto import start_end_to_segments, segments_to_start_end
from pycbc.events.veto import indices_within_times

# get coinc HL time so we can select that for use as background
hsegs = []
lsegs = []
for s, e in [(1126051217, 1137254417), (1164556817, 1187733618), (1238166018, 1253977218), (1253977219, 1320363336)]:
    hsegs +=  query_flag('H1', 'DATA', s, e, cache=True)
    lsegs +=  query_flag('L1', 'DATA', s, e, cache=True)

cseg = (hsegs & lsegs).coalesce()
cstart, cend = segments_to_start_end(cseg)
cstart.sort()
cend.sort()
print((cend - cstart).sum())

        
te = [1263097407.74, 1187008882.45]
te = numpy.array(te)
from astropy.time import Time
import numpy


for i1, run in enumerate(['nsbh', 'bns']):
    f, axs = pylab.subplots(2, 1, dpi=200, sharex=True, sharey=True)
    for i2, ifo in enumerate(['H1', 'L1']):
        pylab.sca(axs[i2])

        if ifo == 'H1':
            pylab.text(.5,.9, run.upper(), fontsize=15,
                   horizontalalignment='center',
                   transform=pylab.gca().transAxes)
            
        t, s, vtid, vchisq, vsg, m1, m2, snr = data[(run, ifo)]    
        #k = m1 + m2 < 150
        #t = t[k]
        #s = s[k]
        #m1 = m1[k]
        #m2 = m2[k]
        #vchisq = vchisq[k]
        #vsg = vsg[k]
        #snr = snr[k]
     
        gws = indices_within_times(t, te - 1.0, te + 1.0)
        nongw = indices_outside_times(t, te - 1.0, te + 1.0)
        
        hl = indices_within_times(t, cstart, cend)
        
        gws = gws[numpy.isin(gws, hl)]
        
        bkg = nongw[numpy.isin(nongw, hl)]
        can = nongw[~numpy.isin(nongw, hl)]
        
        bkg = bkg[indices_within_times(t[bkg], [1238166018], [1320363336])]
        gws = gws[indices_within_times(t[gws], [1238166018], [1320363336])]
        can = can[indices_within_times(t[can], [1238166018], [1320363336])] 
        
        bins = numpy.arange(7.0, s.max()*1.2, .2)
        
        pylab.hist([s[bkg], s[can],  s[gws]], bins=bins,
                   label=('Background','Candidates',  'Multi-detector GWs', ),
                   alpha=1.0, stacked=True, histtype='bar')
        
        #print(x)
        #print(s[can].max())
        if i2 == 0:
            pylab.legend()
            pylab.text(7.7, 3000, "LIGO Hanford")
        else:
            pylab.text(7.7, 3000, "LIGO Livingston")
            pylab.xlabel('Re-weighted SNR ($\\tilde{\\rho}$)', fontsize=14)
        
        pylab.yscale('log')
        pylab.xlim(xmin=7.0, xmax=13.0)
        pylab.ylim(0.5, 10000)

        pylab.gca().tick_params(axis='both', which='major', labelsize=12)
        #print(run, ifo)
        #print()
        top = s[can].argsort()[-5:]
        pnum = 0
        for i in top:
            if s[can][i] > 9.0:
                stat = s[can][i]
                dt = Time(t[can][i], scale='utc', format='gps').datetime
                
                name = 'GW{:02d}{:02d}{:02d}\_{:02d}{:02d}{:02d}'.format(dt.year-2000,
                                                     dt.month,
                                                     dt.day,
                                                     dt.hour,
                                                     dt.minute,
                                                     dt.second,
                                                    )

                pylab.annotate(name, xy=(stat, 1.2), xytext=(stat - 0.5, 30 / 4 ** pnum),
                               arrowprops=dict(facecolor='black', frac=.001,
                                               headwidth=4, width=1, alpha=0.25),
                               )
                pnum += 1
            
            dt = Time(t[can][i], format='gps', scale='utc').datetime
            print("%s, %s, %2.2f %2.2f %2.2f %2.2f %2.2f %2.2f" % (dt,  t[can][i],
                    s[can][i], snr[can][i], vchisq[can][i], vsg[can][i], m1[can][i], m2[can][i]))
            
    pylab.tight_layout()
    pylab.savefig('{}_single.pdf'.format(run))            

32004597
2019-06-11 02:34:26.354980, 1244255684.3549805, 8.04 7.97 1.00 1.00 1.23 2.30
2019-09-13 20:51:00.699219, 1252443078.6992188, 8.11 8.10 0.90 1.00 1.02 17.36
2019-11-05 04:25:26.926758, 1256963144.9267578, 8.11 7.85 1.02 1.00 1.21 10.21
2019-11-14 22:50:37.885742, 1257807055.8857422, 8.25 9.17 1.40 0.20 1.30 29.62
2019-04-19 10:40:52.979492, 1239705670.9794922, 8.27 8.34 0.95 1.00 1.00 3.20
2019-09-15 21:27:33.567871, 1252618071.567871, 8.33 8.61 1.03 1.00 1.07 3.89
2019-07-22 01:16:39.755371, 1247793417.755371, 8.36 8.50 0.86 1.00 1.51 6.15
2019-07-31 21:23:07.310547, 1248643405.3105469, 8.49 8.27 0.98 1.00 1.35 4.24
2019-04-25 08:18:05.020508, 1240215503.0205078, 11.14 11.98 1.26 1.00 1.01 3.06
2020-01-05 16:24:26.058105, 1262276684.0581055, 11.92 13.30 1.28 1.00 1.55 13.72


/tmp/ipykernel_139522/1727537435.py:106: UserWarning: 'frac' option in 'arrowprops' is no longer supported; use 'headlength' to set the head length in points.
  pylab.tight_layout()
/tmp/ipykernel_139522/1727537435.py:107: UserWarning: 'frac' option in 'arrowprops' is no longer supported; use 'headlength' to set the head length in points.
  pylab.savefig('{}_single.pdf'.format(run))


2019-11-11 11:37:05.529297, 1257507443.5292969, 7.76 7.79 0.97 1.00 1.97 1.07
2019-07-12 18:37:26.315430, 1246991864.3154297, 7.80 8.12 1.09 1.00 1.44 1.15
2019-12-26 22:12:21.002930, 1261433559.0029297, 7.81 8.09 1.03 1.00 1.64 1.98
2019-07-13 01:22:31.274902, 1247016169.2749023, 7.84 7.79 0.95 1.00 1.20 1.04
2019-06-11 02:34:26.354492, 1244255684.3544922, 7.98 8.02 0.96 1.00 1.84 1.51
2019-09-11 14:09:52.594727, 1252246210.5947266, 8.01 8.40 1.17 1.00 1.39 1.26
2019-05-05 04:35:24.089844, 1241066142.0898438, 8.03 8.00 0.97 1.00 1.81 1.69
2019-09-26 20:15:38.061523, 1253564156.0615234, 8.08 8.48 1.17 1.00 1.08 1.85
2019-09-09 17:58:06.255371, 1252087104.255371, 8.45 8.17 0.87 1.00 1.10 1.00
2019-04-25 08:18:05.018555, 1240215503.0185547, 11.02 11.92 1.27 1.00 1.71 1.71
